In [1]:
import os
import sys
import re
import pandas as pd
import commands
import ast
import itertools
import pyspark.sql.functions
from pyspark.sql.functions import col
from datetime import datetime
from collections import Counter
import re
import numpy as np
#from pyspark.sql import SparkSession
spark_home = os.environ.get('SPARK_HOME', None)
if not spark_home:
    raise ValueError('SPARK_HOME environment variable is not set')
if not os.path.isdir(spark_home):
    raise ValueError('SPARK_HOME environment variable is not a directory')
if not os.path.isdir(os.path.join(spark_home, 'python')):
    raise ValueError('SPARK_HOME directory does not contain python')
sys.path.insert(0, os.path.join(spark_home, 'python'))
pylib_list = (item for item in os.listdir(os.path.join(spark_home, 'python/lib/'))
              if re.match(r'py4j-\d+(\.\d+)+-src\.zip\Z', item)
              )
try:
    py4j_file = max(pylib_list)
    py4j = os.path.join(spark_home, os.path.join('python/lib', py4j_file))
except ValueError:
    raise ValueError(
        'Could not find py4j'
    )
sys.path.insert(0, py4j)

spark_release_file = spark_home + "/RELEASE"
if os.path.exists(spark_release_file) and "Spark" in  open(spark_release_file).read():
    pyspark_submit_args = os.environ.get("PYSPARK_SUBMIT_ARGS", " --master yarn-client \
                                         --executor-memory 4g --executor-cores 5 --driver-memory 16g"
                                        )
    if not "pyspark-shell" in pyspark_submit_args: pyspark_submit_args += " pyspark-shell"
    os.environ["PYSPARK_SUBMIT_ARGS"] = pyspark_submit_args

with open(os.path.join(spark_home, 'python/pyspark/shell.py')) as f:
    code = compile(f.read(), os.path.join(spark_home, 'python/pyspark/shell.py'), 'exec')
    exec(code)


Welcome to
      ____              __
     / __/__  ___ _____/ /__
    _\ \/ _ \/ _ `/ __/  '_/
   /__ / .__/\_,_/_/ /_/\_\   version 2.3.0.2.6.5.0-292
      /_/

Using Python version 2.7.15 (default, May  1 2018 23:32:55)
SparkSession available as 'spark'.


In [2]:
sqlContext.sql("use dsc60230_gcct_tz_db")

DataFrame[]

In [4]:
sqlContext.tables("dsc60230_gcct_tz_db").where("tableName not like '%temptz%'").show(1000,False)

+-------------------+--------------------------------------+-----------+
|database           |tableName                             |isTemporary|
+-------------------+--------------------------------------+-----------+
|dsc60230_gcct_tz_db|account                               |false      |
|dsc60230_gcct_tz_db|activityparty                         |false      |
|dsc60230_gcct_tz_db|annotation                            |false      |
|dsc60230_gcct_tz_db|appointment                           |false      |
|dsc60230_gcct_tz_db|attributemetadata                     |false      |
|dsc60230_gcct_tz_db|bad_record                            |false      |
|dsc60230_gcct_tz_db|businessunit                          |false      |
|dsc60230_gcct_tz_db|calendar                              |false      |
|dsc60230_gcct_tz_db|calendarrule                          |false      |
|dsc60230_gcct_tz_db|contact                               |false      |
|dsc60230_gcct_tz_db|cxlvhlp_chatactivity          

In [8]:
sqlContext.table("annotation").columns.sort()

In [180]:
sqlContext.table("incident").where("incident_identity >700").select("incident_identity").show(100,False)

+-----------------+
|incident_identity|
+-----------------+
|64194            |
|64196            |
|64202            |
|64199            |
|64197            |
|64207            |
|64197            |
|64200            |
|64204            |
|64206            |
|64202            |
|64195            |
|64203            |
|64198            |
|64195            |
|64201            |
|64198            |
|64196            |
|64205            |
|64203            |
|64246            |
|64239            |
|64237            |
|64217            |
|63846            |
|64226            |
|62185            |
|64211            |
|62349            |
|64257            |
|64249            |
|64253            |
|64222            |
|64256            |
|64252            |
|64213            |
|64248            |
|64211            |
|64214            |
|64251            |
|63507            |
|64228            |
|64216            |
|64235            |
|64212            |
|64232            |
|64247            |


In [4]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            a=sqlCtx.table(k).columns
            a.sort()
            for i in a:
                print k,i

account account_identity
account account_rowversion
account accountcategorycode
account accountclassificationcode
account accountid
account accountnumber
account accountratingcode
account address1_addressid
account address1_addresstypecode
account address1_city
account address1_composite
account address1_country
account address1_county
account address1_fax
account address1_freighttermscode
account address1_latitude
account address1_line1
account address1_line2
account address1_line3
account address1_longitude
account address1_name
account address1_postalcode
account address1_postofficebox
account address1_primarycontactname
account address1_shippingmethodcode
account address1_stateorprovince
account address1_telephone1
account address1_telephone2
account address1_telephone3
account address1_upszone
account address1_utcoffset
account address2_addressid
account address2_addresstypecode
account address2_city
account address2_composite
account address2_country
account address2_county
accou

appointment activityadditionalparams
appointment activityid
appointment activitytypecode
appointment actualdurationminutes
appointment actualend
appointment actualstart
appointment appointment_identity
appointment appointment_rowversion
appointment attachmentcount
appointment attachmenterrors
appointment category
appointment createdby
appointment createdby_entitytype
appointment createdbyname
appointment createdbyyominame
appointment createdon
appointment createdonbehalfby
appointment createdonbehalfby_entitytype
appointment createdonbehalfbyname
appointment createdonbehalfbyyominame
appointment description
appointment entitystring
appointment exchangerate
appointment gcct_appointmentresolvedbyid
appointment gcct_appointmentresolvedbyid_entitytype
appointment gcct_appointmentresolvedbyidname
appointment gcct_completewithoutactivity
appointment gcct_customerportal
appointment gcct_dealerportal
appointment gcct_description
appointment gcct_emailfollowup
appointment gcct_emailfollowup_ent

contact accountid
contact accountid_entitytype
contact accountidname
contact accountidyominame
contact accountrolecode
contact address1_addressid
contact address1_addresstypecode
contact address1_city
contact address1_composite
contact address1_country
contact address1_county
contact address1_fax
contact address1_freighttermscode
contact address1_latitude
contact address1_line1
contact address1_line2
contact address1_line3
contact address1_longitude
contact address1_name
contact address1_postalcode
contact address1_postofficebox
contact address1_primarycontactname
contact address1_shippingmethodcode
contact address1_stateorprovince
contact address1_telephone1
contact address1_telephone2
contact address1_telephone3
contact address1_upszone
contact address1_utcoffset
contact address2_addressid
contact address2_addresstypecode
contact address2_city
contact address2_composite
contact address2_country
contact address2_county
contact address2_fax
contact address2_freighttermscode
contact add

cxlvhlp_chatqueuestatistic createdby
cxlvhlp_chatqueuestatistic createdby_entitytype
cxlvhlp_chatqueuestatistic createdbyname
cxlvhlp_chatqueuestatistic createdbyyominame
cxlvhlp_chatqueuestatistic createdon
cxlvhlp_chatqueuestatistic createdonbehalfby
cxlvhlp_chatqueuestatistic createdonbehalfby_entitytype
cxlvhlp_chatqueuestatistic createdonbehalfbyname
cxlvhlp_chatqueuestatistic createdonbehalfbyyominame
cxlvhlp_chatqueuestatistic cxlvhlp_averageavailableslots
cxlvhlp_chatqueuestatistic cxlvhlp_averagequeuesize
cxlvhlp_chatqueuestatistic cxlvhlp_chatqueuestatistic_identity
cxlvhlp_chatqueuestatistic cxlvhlp_chatqueuestatistic_rowversion
cxlvhlp_chatqueuestatistic cxlvhlp_chatqueuestatisticid
cxlvhlp_chatqueuestatistic cxlvhlp_chatsabandoned
cxlvhlp_chatqueuestatistic cxlvhlp_name
cxlvhlp_chatqueuestatistic cxlvhlp_skillid
cxlvhlp_chatqueuestatistic cxlvhlp_skillname
cxlvhlp_chatqueuestatistic cxlvhlp_totalwaittimebeforeabandonment
cxlvhlp_chatqueuestatistic cxlvhlp_windowendtime
cxl

fax activityid
fax activitytypecode
fax actualdurationminutes
fax actualend
fax actualstart
fax billingcode
fax category
fax coverpagename
fax createdby
fax createdby_entitytype
fax createdbyname
fax createdbyyominame
fax createdon
fax createdonbehalfby
fax createdonbehalfby_entitytype
fax createdonbehalfbyname
fax createdonbehalfbyyominame
fax description
fax directioncode
fax entitystring
fax exchangerate
fax fax_identity
fax fax_rowversion
fax faxnumber
fax from
fax gcct_initiatinguser
fax id
fax importsequencenumber
fax isbilled
fax isregularactivity
fax isworkflowcreated
fax lastonholdtime
fax lastupdatedatetime
fax lastupdtby
fax message__id
fax modifiedby
fax modifiedby_entitytype
fax modifiedbyname
fax modifiedbyyominame
fax modifiedon
fax modifiedonbehalfby
fax modifiedonbehalfby_entitytype
fax modifiedonbehalfbyname
fax modifiedonbehalfbyyominame
fax numberofpages
fax onholdtime
fax overriddencreatedon
fax ownerid
fax ownerid_entitytype
fax owneridname
fax owneridtype
fax own

...

msdyn_survey createdby
msdyn_survey createdby_entitytype
msdyn_survey createdbyname
msdyn_survey createdbyyominame
msdyn_survey createdon
msdyn_survey createdonbehalfby
msdyn_survey createdonbehalfby_entitytype
msdyn_survey createdonbehalfbyname
msdyn_survey createdonbehalfbyyominame
msdyn_survey emailaddress
msdyn_survey entityimage_timestamp
msdyn_survey entityimage_url
msdyn_survey entityimageid
msdyn_survey entitystring
msdyn_survey id
msdyn_survey importsequencenumber
msdyn_survey lastupdatedatetime
msdyn_survey lastupdtby
msdyn_survey message__id
msdyn_survey modifiedby
msdyn_survey modifiedby_entitytype
msdyn_survey modifiedbyname
msdyn_survey modifiedbyyominame
msdyn_survey modifiedon
msdyn_survey modifiedonbehalfby
msdyn_survey modifiedonbehalfby_entitytype
msdyn_survey modifiedonbehalfbyname
msdyn_survey modifiedonbehalfbyyominame
msdyn_survey msdyn_abbreviation
msdyn_survey msdyn_acceptanonymousresponses
msdyn_survey msdyn_addtositemap
msdyn_survey msdyn_alertlowertarget
msd

msdyn_surveyresponse createdby
msdyn_surveyresponse createdby_entitytype
msdyn_surveyresponse createdbyname
msdyn_surveyresponse createdbyyominame
msdyn_surveyresponse createdon
msdyn_surveyresponse createdonbehalfby
msdyn_surveyresponse createdonbehalfby_entitytype
msdyn_surveyresponse createdonbehalfbyname
msdyn_surveyresponse createdonbehalfbyyominame
msdyn_surveyresponse emailaddress
msdyn_surveyresponse entitystring
msdyn_surveyresponse gcct_keywords
msdyn_surveyresponse gcct_rootcause
msdyn_surveyresponse gcct_score
msdyn_surveyresponse gcct_sentimentoptioncode
msdyn_surveyresponse id
msdyn_surveyresponse importsequencenumber
msdyn_surveyresponse lastupdatedatetime
msdyn_surveyresponse lastupdtby
msdyn_surveyresponse message__id
msdyn_surveyresponse modifiedby
msdyn_surveyresponse modifiedby_entitytype
msdyn_surveyresponse modifiedbyname
msdyn_surveyresponse modifiedbyyominame
msdyn_surveyresponse modifiedon
msdyn_surveyresponse modifiedonbehalfby
msdyn_surveyresponse modifiedonb

queue emailaddress
queue emailpassword
queue emailrouteraccessapproval
queue emailusername
queue entityimage_timestamp
queue entityimage_url
queue entityimageid
queue entitystring
queue exchangerate
queue gcct_enabledforgetnext
queue id
queue ignoreunsolicitedemail
queue importsequencenumber
queue incomingemaildeliverymethod
queue incomingemailfilteringmethod
queue isemailaddressapprovedbyo365admin
queue isfaxqueue
queue lastupdatedatetime
queue lastupdtby
queue message__id
queue modifiedby
queue modifiedby_entitytype
queue modifiedbyname
queue modifiedbyyominame
queue modifiedon
queue modifiedonbehalfby
queue modifiedonbehalfby_entitytype
queue modifiedonbehalfbyname
queue modifiedonbehalfbyyominame
queue name
queue numberofitems
queue numberofmembers
queue organizationid
queue organizationid_entitytype
queue organizationidname
queue outgoingemaildeliverymethod
queue overriddencreatedon
queue ownerid
queue ownerid_entitytype
queue owneridname
queue owneridtype
queue owneridyominame
qu

socialactivity actualdurationminutes
socialactivity actualend
socialactivity actualstart
socialactivity community
socialactivity createdby
socialactivity createdby_entitytype
socialactivity createdon
socialactivity createdonbehalfby
socialactivity createdonbehalfby_entitytype
socialactivity createdonbehalfbyname
socialactivity createdonbehalfbyyominame
socialactivity description
socialactivity directioncode
socialactivity entitystring
socialactivity exchangerate
socialactivity from
socialactivity id
socialactivity importsequencenumber
socialactivity inresponseto
socialactivity isbilled
socialactivity isregularactivity
socialactivity isworkflowcreated
socialactivity lastonholdtime
socialactivity lastupdatedatetime
socialactivity lastupdtby
socialactivity message__id
socialactivity modifiedby
socialactivity modifiedby_entitytype
socialactivity modifiedon
socialactivity modifiedonbehalfby
socialactivity modifiedonbehalfby_entitytype
socialactivity modifiedonbehalfbyname
socialactivity mod

team administratorid
team administratorid_entitytype
team administratoridname
team administratoridyominame
team businessunitid
team businessunitid_entitytype
team businessunitidname
team createdby
team createdby_entitytype
team createdbyname
team createdbyyominame
team createdon
team createdonbehalfby
team createdonbehalfby_entitytype
team createdonbehalfbyname
team createdonbehalfbyyominame
team description
team emailaddress
team entitystring
team exchangerate
team gcct_accountbasedworkloadassignment
team gcct_allowdealerstoviewotherdealercases
team gcct_autocaseclosedispositiontype
team gcct_autocaseclosedispositiontype_entitytype
team gcct_autocaseclosedispositiontypename
team gcct_autoclosecasetimelimit
team gcct_businessteamtype
team gcct_canownemployeerecord
team gcct_canreopencase
team gcct_caseassignmentfetchxmlcondition
team gcct_casereopentimelimit
team gcct_country
team gcct_country_entitytype
team gcct_countryname
team gcct_defaultcontactaccountsetting
team gcct_displaycase

In [11]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            a=sqlCtx.table(k).columns
            a.sort()
            for n in a:
                if "skill" in str(n):
                    print k,n

cxlvhlp_chatactivity cxlvhlp_skill
cxlvhlp_chatqueuestatistic cxlvhlp_skillid
cxlvhlp_chatqueuestatistic cxlvhlp_skillname
systemuser skills


In [5]:
print("data_captured_on,11/29/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,11/29/2018
Table,Data(rows)
account,57
activityparty,0
annotation,40
appointment,22
attributemetadata,0
bad_record,4698
businessunit,0
calendar,0
calendarrule,0
contact,398
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,0
cxlvhlp_surveyitem,0
deletelog,0
email,569
fax,0
gcct_additionalsymptomcodes,0
gcct_addportalmessage,0
gcct_arbitrationclaimprocessing,0
gcct_buybackevaluationmilestones,0
gcct_caseassignment,0
gcct_caseclassification,0
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,0
gcct_customersatisfactiontools,0
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,0
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,0
gcct_fieldinvolvementassistancerequest,0
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,0
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,0
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost,0
gcct_loyaltyassista

In [4]:
print("data_captured_on,11/30/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,11/30/2018
Table,Data(rows)
account,57
activityparty,0
annotation,40
appointment,22
attributemetadata,0
bad_record,4990
businessunit,0
calendar,0
calendarrule,0
contact,398
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,0
cxlvhlp_surveyitem,0
deletelog,0
email,569
fax,0
gcct_additionalsymptomcodes,0
gcct_addportalmessage,0
gcct_arbitrationclaimprocessing,0
gcct_buybackevaluationmilestones,0
gcct_caseassignment,0
gcct_caseclassification,0
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,0
gcct_customersatisfactiontools,0
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,0
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,0
gcct_fieldinvolvementassistancerequest,0
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,0
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,0
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost,0
gcct_loyaltyassista

In [5]:
print("data_captured_on,12/03/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/03/2018
Table,Data(rows)
account,129
activityparty,0
annotation,1165
appointment,51
attributemetadata,0
bad_record,12038
businessunit,0
calendar,0
calendarrule,0
contact,649
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,0
cxlvhlp_surveyitem,0
deletelog,0
email,705
fax,0
gcct_additionalsymptomcodes,0
gcct_addportalmessage,0
gcct_arbitrationclaimprocessing,0
gcct_buybackevaluationmilestones,0
gcct_caseassignment,0
gcct_caseclassification,0
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,0
gcct_customersatisfactiontools,0
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,0
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,0
gcct_fieldinvolvementassistancerequest,0
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,0
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,0
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost,0
gcct_loyaltyass

In [5]:
print("data_captured_on,12/04/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/04/2018
Table,Data(rows)
account,279
activityparty,1160
annotation,1217
appointment,56
attributemetadata,0
bad_record,12923
businessunit,0
calendar,0
calendarrule,0
contact,818
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,0
cxlvhlp_surveyitem,0
deletelog,0
email,729
fax,0
gcct_additionalsymptomcodes,0
gcct_addportalmessage,0
gcct_arbitrationclaimprocessing,0
gcct_buybackevaluationmilestones,0
gcct_caseassignment,0
gcct_caseclassification,0
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,0
gcct_customersatisfactiontools,0
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,0
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,0
gcct_fieldinvolvementassistancerequest,0
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,0
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,0
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost,0
gcct_loyalty

In [4]:
print("data_captured_on,12/05/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/05/2018
Table,Data(rows)
account,294
activityparty,4094
annotation,1221
appointment,68
attributemetadata,0
bad_record,22360
businessunit,0
calendar,2
calendarrule,0
contact,850
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,0
deletelog,0
email,1085
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,0
gcct_arbitrationclaimprocessing,14
gcct_buybackevaluationmilestones,17
gcct_caseassignment,304
gcct_caseclassification,8
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,0
gcct_customersatisfactiontools,6
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,17
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,19
gcct_fieldinvolvementassistancerequest,15
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,44
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,10
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost,0


In [6]:
print("data_captured_on,12/06/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/06/2018
Table,Data(rows)
account,355
activityparty,4842
annotation,1229
appointment,71
attributemetadata,0
bad_record,22366
businessunit,0
calendar,10
calendarrule,0
contact,891
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,0
deletelog,0
email,1290
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,1
gcct_arbitrationclaimprocessing,17
gcct_buybackevaluationmilestones,21
gcct_caseassignment,497
gcct_caseclassification,213
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,7
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,22
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,23
gcct_fieldinvolvementassistancerequest,17
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,49
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,12
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercost

In [5]:
print("data_captured_on,12/07/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/07/2018
Table,Data(rows)
account,370
activityparty,5381
annotation,1235
appointment,76
attributemetadata,0
bad_record,22396
businessunit,0
calendar,449
calendarrule,7
contact,921
cxlvhlp_chatactivity,1
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,3
deletelog,0
email,1490
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,1
gcct_arbitrationclaimprocessing,22
gcct_buybackevaluationmilestones,26
gcct_caseassignment,621
gcct_caseclassification,213
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,7
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,26
gcct_doaprogramcode,0
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,30
gcct_fieldinvolvementassistancerequest,19
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,57
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,13
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercos

In [3]:
print("data_captured_on,12/10/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/10/2018
Table,Data(rows)
account,380
activityparty,5712
annotation,1244
appointment,76
attributemetadata,0
bad_record,22396
businessunit,0
calendar,451
calendarrule,7
contact,949
cxlvhlp_chatactivity,1
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,3
deletelog,0
email,1495
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,1
gcct_arbitrationclaimprocessing,24
gcct_buybackevaluationmilestones,27
gcct_caseassignment,703
gcct_caseclassification,213
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,7
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,26
gcct_doaprogramcode,1
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,31
gcct_fieldinvolvementassistancerequest,21
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,58
gcct_genericinformationtopic,0
gcct_generictopic,0
gcct_goodfaithreview,14
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanercos

In [4]:
print("data_captured_on,12/11/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/11/2018
Table,Data(rows)
account,380
activityparty,8960
annotation,1244
appointment,83
attributemetadata,0
bad_record,22439
businessunit,0
calendar,451
calendarrule,7
contact,1013
cxlvhlp_chatactivity,1
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,3
deletelog,0
email,1505
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,1
gcct_arbitrationclaimprocessing,26
gcct_buybackevaluationmilestones,32
gcct_caseassignment,881
gcct_caseclassification,4527
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,9
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,31
gcct_doaprogramcode,1
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,31
gcct_fieldinvolvementassistancerequest,21
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,62
gcct_genericinformationtopic,2
gcct_generictopic,1
gcct_goodfaithreview,14
gcct_knownpartsdelay,0
gcct_lemonlawcriteria,0
gcct_loanerc

In [16]:
print("data_captured_on,12/13/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/13/2018
Table,Data(rows)
account,380
activityparty,9753
annotation,1253
appointment,89
attributemetadata,0
bad_record,22486
businessunit,0
calendar,451
calendarrule,7
contact,1068
cxlvhlp_chatactivity,1
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,3
deletelog,0
email,1518
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,2
gcct_arbitrationclaimprocessing,27
gcct_buybackevaluationmilestones,41
gcct_caseassignment,1060
gcct_caseclassification,4527
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,13
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,36
gcct_doaprogramcode,1
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,38
gcct_fieldinvolvementassistancerequest,23
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,73
gcct_genericinformationtopic,9
gcct_generictopic,6
gcct_goodfaithreview,16
gcct_knownpartsdelay,12
gcct_lemonlawcriteria,1
gcct_loan

In [9]:
print("data_captured_on,12/18/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,12/18/2018
Table,Data(rows)
account,385
activityparty,9841
annotation,1262
appointment,90
attributemetadata,0
bad_record,108851
businessunit,0
calendar,451
calendarrule,7
contact,1098
cxlvhlp_chatactivity,1
cxlvhlp_chatqueuestatistic,35
cxlvhlp_surveyitem,3
deletelog,0
email,1522
fax,25
gcct_additionalsymptomcodes,0
gcct_addportalmessage,4
gcct_arbitrationclaimprocessing,27
gcct_buybackevaluationmilestones,41
gcct_caseassignment,1088
gcct_caseclassification,4527
gcct_casedispositiontype,0
gcct_coachback,0
gcct_country,1
gcct_customersatisfactiontools,13
gcct_delegationofauthority,0
gcct_demandltrtpsmclaimsprocessing,36
gcct_doaprogramcode,1
gcct_documentcustomerrecontact,0
gcct_engine,0
gcct_executive,0
gcct_executiveliaison,38
gcct_fieldinvolvementassistancerequest,23
gcct_fmcccontract,0
gcct_fulfillmentvendor,0
gcct_genericinformation,74
gcct_genericinformationtopic,9
gcct_generictopic,6
gcct_goodfaithreview,16
gcct_knownpartsdelay,12
gcct_lemonlawcriteria,1
gcct_loa

In [44]:
e1=sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").toPandas()["tableName"]
e2=list(set([i.lower() for sublist in e1 for i in sublist.encode('utf-8').replace("[","").replace("]","").split(", ")]))
for m in sqlContext.tables("dsc24156_fsm_tz_db ").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            if k in e2:
                
                try:
                    sqlCtx.sql("use dsc24156_fsm_tz_db")
                    col_list_fsm=sqlCtx.table(k).columns
                    sqlCtx.sql("use dsc60230_gcct_tz_db")
                    col_list_gcct=sqlCtx.table(k).columns
                    print k,"|".join([str(i) for i in set(col_list_gcct).difference(set(col_list_fsm))]),"|".join([str(i) for i in set(col_list_fsm).difference(set(col_list_gcct))])
                except:
                    print k,"none","none"
                

account msdyusd_twitter|gcct_isinmarket|gcct_marketingmailpreferenceupdatedbyid_entitytype|gcct_dealeractivedate|gcct_allmarketingscores|gcct_defectorscore|gcct_onlineprofileusername|gcct_lincolnterritoryidname|gcct_datasourcesystemname|gcct_dealercontactyominame|gcct_newassignedlincolndealeridname|gcct_newassignedforddealeridyominame|gcct_daylightsavingstime|gcct_usedassignedlincolndealerid_entitytype|gcct_morethanoneservicemanager|gcct_haslikelihoodtoservice|account_rowversion|gcct_geosalescode|gcct_marketingmailpreferenceupdatedbyid|gcct_marketingemailpreferenceupdatedbyid_entitytype|gcct_dealercontactname|gcct_region|gcct_isprimarypacode|gcct_marketingphonepreferenceupdatedbyidname|gcct_dissatscore|gcct_usedassignedlincolndealeridyominame|gcct_dealerservicemanagerid|gcct_ismasterpacode|gcct_dealerservicemanagerid_entitytype|gcct_usedassignedlincolndealerid|gcct_country|gcct_newassignedlincolndealeridyominame|gcct_currentltvscoretext|gcct_usedassignedforddealerid|gcct_dealerservicem

incident gcct_reopenedby_entitytype|gcct_dealeridyominame|gcct_regionidname|gcct_vehiclespecificationfullpath|gcct_allmarketingscores|gcct_symptomclassificationname|gcct_closurecomment|gcct_userid_entitytype|gcct_dealerservicemanager_entitytype|gcct_caseclassificationlevel3_entitytype|gcct_symptomclassificationlevel1|gcct_symptomclassificationlevel3|gcct_symptomclassificationlevel2|gcct_symptomclassificationlevel4|gcct_queueid_entitytype|gcct_vehiclespecificationfullpathname|gcct_useridyominame|gcct_datasourcesystemname|gcct_dealercontactyominame|gcct_caseclassificationteamid_entitytype|gcct_assignmentenddate|gcct_surveysenttocontactyominame|gcct_customerdelegate|gcct_enginespecificationid_entitytype|gcct_bestcontactmethod|gcct_symptomclassificationlevel1_entitytype|gcct_resolvebyslastatus|gcct_symptomclassification|gcct_morethanoneservicemanager|gcct_mileageunits|gcct_contact|gcct_casedispositionteamid_entitytype|incident_identity|gcct_customeraddressline2|gcct_casedispositiontype_ent

systemuser msdyusd_usdconfigurationidname|gcct_primaryteamname|systemuser_rowversion|gcct_primaryteamyominame|gcct_locationid_entitytype|gcct_locationidname|msdyusd_usdconfigurationid_entitytype|msdyusd_usdconfigurationid|gcct_primaryteam|gcct_agentextension|gcct_primaryteam_entitytype|systemuser_identity|gcct_locationid fcs_estimateapprovedby
targetmetadata  


In [38]:
e1=sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").toPandas()["tableName"]
e2=list(set([i.lower() for sublist in e1 for i in sublist.encode('utf-8').replace("[","").replace("]","").split(", ")]))


{'account',
 'activityparty',
 'annotation',
 'appointment',
 'attributemetadata',
 'bad_record',
 'businessunit',
 'calendar',
 'calendarrule',
 'contact',
 'cxlvhlp_chatactivity',
 'cxlvhlp_chatqueuestatistic',
 'cxlvhlp_surveyitem',
 'deletelog',
 'email',
 'fax',
 'gcct_additionalsymptomcodes',
 'gcct_addportalmessage',
 'gcct_arbitrationclaimprocessing',
 'gcct_buybackevaluationmilestones',
 'gcct_caseassignment',
 'gcct_caseclassification',
 'gcct_casedispositiontype',
 'gcct_coachback',
 'gcct_country',
 'gcct_customersatisfactiontools',
 'gcct_delegationofauthority',
 'gcct_demandltrtpsmclaimsprocessing',
 'gcct_doaprogramcode',
 'gcct_documentcustomerrecontact',
 'gcct_engine',
 'gcct_executive',
 'gcct_executiveliaison',
 'gcct_fieldinvolvementassistancerequest',
 'gcct_fmcccontract',
 'gcct_fulfillmentvendor',
 'gcct_genericinformation',
 'gcct_genericinformationtopic',
 'gcct_generictopic',
 'gcct_goodfaithreview',
 'gcct_knownpartsdelay',
 'gcct_lemonlawcriteria',
 'gcct_l

In [39]:
sqlCtx.sql("select gcct_vehicleid from gcct_vehicle ").distinct().where("gcct_vehicleid like '%2F%'").show(1000,False)

+------------------------------------+
|gcct_vehicleid                      |
+------------------------------------+
|E2FD48D8-0DE9-E811-A97E-000D3A37D634|
|93B18DF7-2FEF-E811-A969-000D3A328ED9|
|8C698D20-92F4-E811-A970-000D3A328908|
|C72F51AA-A3EC-E811-A968-000D3A34AE50|
|FA2F7DC2-EB96-E811-A83D-000D3A37CC26|
+------------------------------------+



In [10]:
sqlCtx.sql('select datatype,reason,count(*) from bad_record group by 1,2').show(100,False)

+--------------------------------------+----------------------------------------------------------------+--------+
|datatype                              |reason                                                          |count(1)|
+--------------------------------------+----------------------------------------------------------------+--------+
|gcct_slaconfiguration                 |Error Parsing gcct_slaconfiguration                             |63      |
|gcct_doaprogramcode                   |Error Parsing gcct_doaprogramcode                               |193     |
|gcct_executiveliaison                 |Error Parsing gcct_executiveliaison                             |24      |
|systemuser                            |Duplicate Record. Similar record with same ShaKey already exists|265     |
|Entity                                |Invalid Entity                                                  |1618    |
|gcctcustomersatisfactiontools         |Error Parsing gcctcustomersatisfactionto

In [9]:
sqlCtx.sql('select * from bad_record where datatype="gcctrentaldetail"').show(100,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [20]:
sqlCtx.sql("select fullname,gcct_sourcesystemid,telephone2,address1_line1,address1_postalcode,address1_stateorprovince from contact where address1_line1 like '%Rockddale%'").show(1000,False)

+-----------+-------------------+----------+-----------------+-------------------+------------------------+
|fullname   |gcct_sourcesystemid|telephone2|address1_line1   |address1_postalcode|address1_stateorprovince|
+-----------+-------------------+----------+-----------------+-------------------+------------------------+
|Nani Atluri|10055458353        |3138454901|4432 Rockddale Ct|48085              |mi                      |
+-----------+-------------------+----------+-----------------+-------------------+------------------------+



In [6]:
sqlCtx.sql("select fullname,gcct_sourcesystemid,telephone2,address1_line1,address1_postalcode,address1_stateorprovince from contact where address1_line1 like '%Rockddale%'").show(1000,False)

+-----------+-------------------+----------+-----------------+-------------------+------------------------+
|fullname   |gcct_sourcesystemid|telephone2|address1_line1   |address1_postalcode|address1_stateorprovince|
+-----------+-------------------+----------+-----------------+-------------------+------------------------+
|Nani Atluri|10055458353        |2484271449|4432 Rockddale Ct|48085              |mi                      |
|Nani Atluri|10055458353        |2484271449|4432 Rockddale Ct|48085              |mi                      |
|Nani Atluri|10055458353        |3138454901|4432 Rockddale Ct|48085              |mi                      |
+-----------+-------------------+----------+-----------------+-------------------+------------------------+



In [6]:
sqlCtx.sql("select title,workeridyominame from queueitem where title like '%CAS-202524-D5P0Y4%'").show(10,False)

+-----------------+----------------+
|title            |workeridyominame|
+-----------------+----------------+
|CAS-202524-D5P0Y4|Srinivasa Gadde |
+-----------------+----------------+



In [9]:
sqlCtx.sql("select customeridyominame,gcct_caseclassificationlevel4name,gcct_caseclassificationlevel1name,gcct_caseclassificationlevel2name,gcct_caseclassificationlevel3name from incident where entitystring like '%CAS-202524-D5P0Y4%'").show(10,False)

+------------------+----------------------------------------+---------------------------------+---------------------------------+---------------------------------+
|customeridyominame|gcct_caseclassificationlevel4name       |gcct_caseclassificationlevel1name|gcct_caseclassificationlevel2name|gcct_caseclassificationlevel3name|
+------------------+----------------------------------------+---------------------------------+---------------------------------+---------------------------------+
|MARC ORTEGA       |12 Model Years or Newer<310338345776466>|Vehicle Concern                  |Buyback Request<3103383>         |California Vehicle<31033834577>  |
+------------------+----------------------------------------+---------------------------------+---------------------------------+---------------------------------+



In [44]:
sqlCtx.sql('select entitystring from queueitem  where entitystring like "%CAS-201945-K7C5Q6%"').show(1000,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [43]:
sqlCtx.sql('select * from bad_record  where data like "%CAS-201945-K7C5Q6%"').show(1000,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [69]:
p2=sqlContext.tables(database).select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").toPandas()["tableName"]

In [70]:
p2.sort_values()
for i in p2:
    print i

account
activityparty
annotation
appointment
attributemetadata
businessunit
calendar
calendarrule
contact
cxlvhlp_chatactivity
cxlvhlp_chatqueuestatistic
cxlvhlp_surveyitem
deletelog
email
fax
gcct_additionalsymptomcodes
gcct_addportalmessage
gcct_arbitrationclaimprocessing
gcct_buybackevaluationmilestones
gcct_caseassignment
gcct_caseclassification
gcct_casedispositiontype
gcct_coachback
gcct_country
gcct_customersatisfactiontools
gcct_delegationofauthority
gcct_demandltrtpsmclaimsprocessing
gcct_doaprogramcode
gcct_documentcustomerrecontact
gcct_engine
gcct_executive
gcct_executiveliaison
gcct_fieldinvolvementassistancerequest
gcct_fmcccontract
gcct_fulfillmentvendor
gcct_genericinformation
gcct_genericinformationtopic
gcct_generictopic
gcct_goodfaithreview
gcct_knownpartsdelay
gcct_lemonlawcriteria
gcct_loanercost
gcct_loyaltyassistance
gcct_loyaltycostdetails
gcct_loyaltyprogramcode
gcct_material
gcct_materialrequest
gcct_materialrequestdetail
gcct_offer
gcct_offerdetail
gcct_onlin

In [25]:
sqlCtx.table("bad_record").where("data like 'workeridyominame'").show(10,False)

+----+--------+--------+------+---------+-----------+-----------+----------+------------------+
|data|datatype|filename|reason|exception|process__id|message__id|lastupdtby|lastupdatedatetime|
+----+--------+--------+------+---------+-----------+-----------+----------+------------------+
+----+--------+--------+------+---------+-----------+-----------+----------+------------------+



In [145]:
k="account"
if k=="account":
            #k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k)

from collections import Counter
import re
def freq(lst):
    d = {}
    for i in lst:
        if d.get(i):
            d[i] += 1
        else:
            d[i] = 1
    return d

v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("{",",").replace("}","").replace(", ",",").replace("=",":").replace("\"","").replace("false","False").replace("true","True").replace("null","None")).map(lambda g: re.sub("datetime.datetime\(.*?\)", "", g)).map(lambda w: w.replace(")","")).take(2)

['account_identity:52,account_rowversion:AAAAAAAA1Xs:,id:None,sinkcreatedon:None,sinkmodifiedon:None,statecode:0,statuscode:1,customertypecode:None,address1_freighttermscode:None,address1_addresstypecode:None,accountclassificationcode:1,shippingmethodcode:1,preferredappointmenttimecode:None,gcct_preferredemail:None,address2_freighttermscode:1,accountcategorycode:None,paymenttermscode:None,businesstypecode:2,industrycode:None,gcct_fleetstatuscode:None,address1_shippingmethodcode:None,preferredappointmentdaycode:None,customersizecode:1,preferredcontactmethodcode:None,accountratingcode:1,gcct_profiletype:None,address2_addresstypecode:1,address2_shippingmethodcode:1,gcct_dealertype:None,ownershipcode:None,territorycode:1,gcct_accountstatus:None,gcct_sourcetype:None,gcct_isprimarypacode:None,gcct_marketingemailpreference:None,donotbulkpostalmail:False,donotpostalmail:False,gcct_isgenericaccount:None,gcct_marketingmailpreference:None,gcct_donotallowcall:False,gcct_isinmarket:None,gcct_haslik

In [167]:
k="annotation"
if k=="annotation":
            #k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k)

from collections import Counter
import re
def freq(lst):
    d = {}
    for i in lst:
        if d.get(i):
            d[i] += 1
        else:
            d[i] = 1
    return d
import re
v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("{",",").replace("}","").replace(", ",",").replace("=",":").replace("\"","").replace("false","False").replace("true","True").replace("null","None")).map(lambda g: re.sub("datetime.datetime\(.*?\)", "", g)).map(lambda w:w.replace(")","")).map(lambda z: z.split(",")).map(lambda y:freq(y)).take(1)

[{'Id:38BA44BB-81F2-E811-A96D-000D3A328903': 1,
  'Id:B29EA435-81F2-E811-A96D-000D3A328903': 1,
  'SinkCreatedOn:2018-11-27T20:16:12': 1,
  'SinkCreatedOn:2018-11-27T20:19:47': 1,
  'SinkModifiedOn:2018-11-27T20:19:34': 1,
  'SinkModifiedOn:2018-11-27T20:19:47': 1,
  'accountid:None': 1,
  'accountid_entitytype:None': 1,
  'accountidname:None': 1,
  'accountidyominame:None': 1,
  'activitiescomplete:False': 1,
  'actualserviceunits:None': 1,
  'adx_createdbyipaddress:None': 1,
  'adx_createdbyusername:None': 1,
  'adx_modifiedbyipaddress:None': 1,
  'adx_modifiedbyusername:None': 1,
  'adx_publishtoweb:False': 1,
  'adx_resolution:None': 1,
  'adx_resolutiondate:None': 1,
  'adx_stepstoreproduce:None': 1,
  'annotation_identity:141': 2,
  'annotation_rowversion:AAAAAAALSHM:': 2,
  'annotationid:38BA44BB-81F2-E811-A96D-000D3A328903': 2,
  'billedserviceunits:None': 1,
  'blockedprofile:False': 1,
  'caseorigincode:1': 1,
  'casetypecode:None': 1,
  'checkemail:False': 1,
  'contact_sour

In [140]:
import re 
x = "datetime.datetime(once a day) [twice a day]"
re.sub("datetime.datetime\(.*?\)", "", x)

' [twice a day]'

In [169]:
k="a"
if k=="annotation":
            #k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k)

from collections import Counter
import re
def freq(lst):
    d = {}
    for i in lst:
        if d.get(i):
            d[i] += 1
        else:
            d[i] = 1
    return d

import re
v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("{",",").replace("}","").replace(", ",",").replace("=",":").replace("\"","").replace("false","False").replace("true","True").replace("null","None")).map(lambda g: re.sub("datetime.datetime\(.*?\)", "", g)).map(lambda w:w.replace(")","")).map(lambda z: re.findall(r',(.*?):', z)).map(lambda y:freq(y)).map(lambda r: [key+str(value) for key, value in r.iteritems() if value>2]).collect()

[['modifiedonbehalfby3',
  'owningteam_entitytype3',
  'owningbusinessunit_entitytype3',
  'modifiedonbehalfbyyominame3',
  'owneridyominame3',
  'importsequencenumber3',
  'modifiedonbehalfbyname3',
  'modifiedby3',
  'createdonbehalfby3',
  'owninguser3',
  'owningbusinessunit3',
  'createdby_entitytype3',
  'modifiedbyname3',
  'owneridtype3',
  'ownerid_entitytype3',
  'ownerid3',
  'createdon3',
  'versionnumber3',
  'createdonbehalfbyyominame3',
  'createdbyname3',
  'owninguser_entitytype3',
  'createdbyyominame3',
  'modifiedon3',
  'modifiedby_entitytype3',
  'overriddencreatedon3',
  'createdonbehalfbyname3',
  'owningteam3',
  'createdby3',
  'modifiedbyyominame3',
  'modifiedonbehalfby_entitytype3',
  'owneridname3',
  'createdonbehalfby_entitytype3'],
 [],
 [],
 ['modifiedonbehalfby3',
  'owningteam_entitytype3',
  'owningbusinessunit_entitytype3',
  'modifiedonbehalfbyyominame3',
  'owneridyominame3',
  'importsequencenumber3',
  'modifiedonbehalfbyname3',
  'modifiedby3'

In [102]:
def freq(lst):
    d = {}
    for i in lst:
        if d.get(i):
            d[i] += 1
        else:
            d[i] = 1
    return d

for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k)
            #print(k)
            v2=v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("\"","")).map(lambda z: re.findall(r',([a-zA-Z]+):{', z))
            try:
                v3=v2.max()
                if v3:
                    print(k,v3)
            except:
                #print("_____________",k)
                pass

('annotation', ['incident'])
('cxlvhlp_chatactivity', ['customer', 'authenticated', 'mobile', 'chat', 'activityadditionalparams', 'customer', 'authenticated', 'mobile', 'chat'])
('email', ['incident'])
('fax', ['incident'])
('gcct_loyaltycostdetails', ['incident'])
('gcct_materialrequest', ['incident'])
('gcct_recall', ['incident'])
('gcct_testdriverequest', ['incident'])
('phonecall', ['incident'])


In [7]:
sqlContext.table("cxlvhlp_chatactivity").show(10,False)

+-----------------------------+-------------------------------+----+-------------+--------------+---------+----------+---------+----------------+--------------------+------------------+-----------------------+------------+-------------------------------+-----------------+--------+-----------------+-------------+-------------+---------------------+-------------------------------+-----+----------------+------------------------------------+-----------------------------+-----------------+----------------------------+------------------------------------+---------------------+------------------+-----------------------------+------------------------------------+---------------------+----------------------+---------------------------------+---------------+--------------------------+-----------------+----------------------------+----------+---------------------+------------+-----------------------+---------------------+--------------------------------+---------------------------+---------------

In [8]:
sqlContext.table("cxlvhlp_chatactivity").select("activityadditionalparams").show(10,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [9]:
sqlContext.sql("desc customer").show(100,False)

AnalysisException: u"Table or view 'customer' not found in database 'dsc60230_gcct_tz_db';"

In [126]:
import re
v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("{",",").replace("}","").replace(")","").replace(", ",",").replace("=",":").replace("\"","").replace("false","False").replace("true","True").replace("null","None").replace("","")).take(1)


[Counter({'11,28,11,3,58,shakey': 1,
          '11,28,12,47,54,adx_modifiedbyipaddress': 1,
          '11,28,12,47,54,overriddencreatedon': 1,
          '11,28,12,47,54,traversedpath': 1,
          '11,28,12,47,57,preferredequipmentidname': 1,
          'Id': 1,
          'MI 48312,gcct_dealerservicemanageridyominame': 1,
          'MI 48312,primarycontactidyominame': 1,
          'SinkCreatedOn': 1,
          'SinkModifiedOn': 1,
          'account_identity': 1,
          'account_rowversion': 2,
          'accountcategorycode': 2,
          'accountclassificationcode': 2,
          'accountid': 2,
          'accountnumber': 2,
          'accountratingcode': 2,
          'address1_addressid': 2,
          'address1_addresstypecode': 2,
          'address1_city': 2,
          'address1_composite': 2,
          'address1_country': 2,
          'address1_county': 2,
          'address1_fax': 2,
          'address1_freighttermscode': 2,
          'address1_latitude': 2,
          'address

In [83]:
v2=v1.rdd.map(lambda x: str(x).replace("Row(","").replace("u\'","").replace("\'","").replace("\\\\","").replace("{",",").replace("}","").replace(")","").replace(", ",",").replace("=",":").replace("\"","").replace("false","False").replace("true","True").replace("null","None"))


['id:None,sinkcreatedon:None,sinkmodifiedon:None,gcct_territorytypecode:None,gcct_csmtypecode:None,gcct_isterritorygroup:False,gcct_csmtypeoptioncode:False,modifiedonbehalfby:None,modifiedonbehalfby_entitytype:None,managerid:None,managerid_entitytype:None,createdonbehalfby:None,createdonbehalfby_entitytype:None,transactioncurrencyid:None,transactioncurrencyid_entitytype:None,gcct_managerid:None,gcct_managerid_entitytype:None,modifiedby:BEBCFE19-2768-E811-A854-000D3A33A431,modifiedby_entitytype:systemuser,createdby:BEBCFE19-2768-E811-A854-000D3A33A431,createdby_entitytype:systemuser,gcct_territorygroup:4BA41D38-A76E-E811-A838-000D3A37C740,gcct_territorygroup_entitytype:territory,organizationid:02A5D234-B479-4642-AB99-924D71545041,organizationid_entitytype:organization,createdonbehalfbyyominame:None,gcct_region:12,transactioncurrencyidname:None,description:None,gcct_territorygroupname:None,entityimage_timestamp:None,name:12,entityimageid:None,importsequencenumber:None,organizationidname:

In [14]:
def get_len_keys(a):
    key_list=[]
    b=ast.literal_eval(a.replace('null','None').replace('false','False').replace('true','True'))
    get_keys(b,key_list,"Main")
    #new_data_columns.extend(list(set(key_list).difference(set(col_list))))
    #return(new_data_columns)
    return(key_list)



def get_keys(b,key_list,type_s):
    if(type_s=="Main"):
        for i in b.keys():
            try:
                key_list.extend(ast.literal_eval(b[i]).keys())
                key_list.append(i)
                get_keys(ast.literal_eval(b[i]),"sub")
            except:
                key_list.append(i)
    elif(type_s=="sub"):
        for i in b.keys():
            try:
                key_list.extend(ast.literal_eval(b[i]).keys())
                get_keys(ast.literal_eval(b[i]),"sub")
            except:
                pass

In [13]:
import pyspark.sql.functions as F
from pyspark.sql.functions import udf
from pyspark.sql.types import MapType, StringType, IntegerType
udf1 = udf(lambda x:get_len_keys(x))


In [29]:
#for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
k="account"
if k=="account":
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k).select("entitystring")
            global col_list2
            col_list=[]
            col_list.extend(sqlCtx.table(k).columns)
            col_list.extend(['entitylogicalname', 'eventtype', 'entityid', 'eventdatetime', 'sourcesystem', 'entitydata', 'messageid','shakey'])
            col_list2=[x.lower() for x in col_list]
            global new_data_columns
            new_data_columns=[]
            df = v1.withColumn('New', udf1(v1.entitystring))
            list1=list(df.select("New").distinct().toPandas()["New"])
            list2=set([i.lower() for sublist in list1 for i in sublist.encode('utf-8').replace("[","").replace("]","").split(", ")])
            #print k+"|"+",".join([str(i) for i in list2])
            print k+"|"+",".join([str(i) for i in set(list2).difference(col_list2)])+"|"+",".join([str(i) for i in set(col_list2).difference(list2)])       

territory||lastupdatedatetime,entitystring,shakey,process__id,message__id,lastupdtby


In [20]:
database="dsc60230_gcct_tz_db"
p1=sqlCtx.sql("select distinct datatype from bad_record where lastupdatedatetime like '%2018-12-04%'").toPandas()["datatype"]
p2=sqlContext.tables(database).select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").toPandas()["tableName"]
p3=list(set([i.encode('utf-8') for i in list(p1)]).difference(set([j.encode('utf-8') for j in list(p2)])))
print"Following tables are added"
for i in p3:
    print i


Following tables are added
gcctrentaldetail
gcctgoodfaithreview
gcctcaseassignment
gcctdemandltrtpsmclaimsprocessing
gcct_annotation
gcctvehicleclass
gccttestdriverequest
gccttechnicalassistancerequest
gcctpcarequest
gcctvehicleloyaltyallowance
msdynsurveyinvite
gcctwarrantyloanerrequest
gcctgenericinformation
gcctvehicle
gcctexecutiveliaison
gcctbuybackevaluationmilestones
cxlvhlpchatqueuestatistic
gcctvehicleoffroad
gcctarbitrationclaimprocessing
gcctravprocessingmilestones
gcctvehicleowner
Entity
gcctloyaltycostdetails
gcctloyaltyassistance
gcctcustomersatisfactiontools
gcctoffer
gcctfieldinvolvementassistancerequest
gcctpartssmeassistancerequest


In [ ]:
database="dsc60230_gcct_tz_db"
for m in sqlContext.tables(database).select('tableName').where("tableName not like '%annotation%'").where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k).where("lastupdatedatetime like '%2018-12-06%'").select("entitystring")
            global col_list2
            col_list=[]
            col_list.extend(sqlCtx.table(k).columns)
            col_list.extend(['entitylogicalname', 'eventtype', 'entityid', 'eventdatetime', 'sourcesystem', 'entitydata', 'messageid','shakey'])
            col_list2=[x.lower() for x in col_list]
            global new_data_columns
            new_data_columns=[]
            df = v1.withColumn('New', udf1(v1.entitystring))
            list1=list(df.select("New").distinct().toPandas()["New"])
            list2=set([i.lower() for sublist in list1 for i in sublist.encode('utf-8').replace("[","").replace("]","").split(", ")])
            list3=set(list2).difference(col_list2)
            list4=set(col_list2).difference(list2)
            if len(list3) > 0:
                print k+"|"+",".join([str(i) for i in list3])+"|"+",".join([str(i) for i in list4])

account|gcct_telephone2,gcct_mastermarketingemailpreference,gcct_mobilephone,gcct_preferredlanguage,gcct_sourcesystemerror,gcct_mastermarketingsmstextpreference,gcct_mastermarketingmailpreference,gcct_mastermarketingphonepreference|entitystring,lastupdatedatetime,shakey,process__id,message__id,lastupdtby
cxlvhlp_chatactivity|gcct_vehicleclassification,gcct_theinteractionwasaboutlevel3_entitytype,gcct_theinteractionwasabout_entitytype,gcct_theinteractionwasaboutlevel2_entitytype,gcct_theinteractionwasaboutlevel3name,gcct_vehicleclassification_entitytype,gcct_comments,gcct_theinteractionwasaboutlevel4name,gcct_agentsurveycompleted,gcct_theinteractionwasaboutlevel4_entitytype,gcct_theinteractionwasaboutlevel1,gcct_theinteractionwasaboutlevel2,gcct_theinteractionwasaboutlevel3,gcct_theinteractionwasaboutlevel4,gcct_theinteractionwasaboutname,gcct_theinteractionwasaboutlevel1_entitytype,gcct_theinteractionwasaboutlevel2name,gcct_theinteractionwasabout,cxlvhlp_endreason,gcct_vehicleclassific

In [109]:

for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k).select("entitystring")
            global col_list
            col_list=[]
            col_list.extend(sqlCtx.table(k).columns)
            col_list.extend(['SinkModifiedOn', 'entitylogicalname', 'eventtype', 'entityid', 'eventdatetime', 'sourcesystem', 'entitydata', 'SinkCreatedOn'])
            global new_data_columns
            new_data_columns=[]
            print(k)
            df = v1.withColumn('New', udf1(v1.entitystring))
            print(df.select("New").distinct().count())

account
2
activityparty
0
annotation
2
appointment
1
attributemetadata
0
businessunit
0
calendar
0
calendarrule
0
contact
1
cxlvhlp_chatactivity
0
cxlvhlp_chatqueuestatistic
0
cxlvhlp_surveyitem
0
deletelog
0
email
2
fax
0
gcct_additionalsymptomcodes
0
gcct_addportalmessage
0
gcct_arbitrationclaimprocessing
0
gcct_buybackevaluationmilestones
0
gcct_caseassignment
0
gcct_caseclassification
0
gcct_casedispositiontype
0
gcct_coachback
0
gcct_country
0
gcct_customersatisfactiontools
0
gcct_delegationofauthority
0
gcct_demandltrtpsmclaimsprocessing
0
gcct_doaprogramcode
0
gcct_documentcustomerrecontact
0
gcct_engine
0
gcct_executive
0
gcct_executiveliaison
0
gcct_fieldinvolvementassistancerequest
0
gcct_fmcccontract
0
gcct_fulfillmentvendor
0
gcct_genericinformation
0
gcct_genericinformationtopic
0
gcct_generictopic
0
gcct_goodfaithreview
0
gcct_knownpartsdelay
0
gcct_lemonlawcriteria
0
gcct_loanercost
0
gcct_loyaltyassistance
0
gcct_loyaltycostdetails
0
gcct_loyaltyprogramcode
0
gcct_mater

In [ ]:

for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k).select("entitystring")
            global col_list
            col_list=[]
            col_list.extend(sqlCtx.table(k).columns)
            col_list.extend(['SinkModifiedOn', 'entitylogicalname', 'eventtype', 'entityid', 'eventdatetime', 'sourcesystem', 'entitydata', 'SinkCreatedOn'])
            global new_data_columns
            new_data_columns=[]
            print(k)
            df = v1.withColumn('New', udf1(v1.entitystring))
            print(df.select("New").distinct().count())

account
2
activityparty
0
annotation
2
appointment
1
attributemetadata
0
businessunit
0
calendar
0
calendarrule
0
contact
1
cxlvhlp_chatactivity
0
cxlvhlp_chatqueuestatistic
0
cxlvhlp_surveyitem
0
deletelog
0
email
2
fax
0
gcct_additionalsymptomcodes
0
gcct_addportalmessage
0
gcct_arbitrationclaimprocessing
0
gcct_buybackevaluationmilestones
0
gcct_caseassignment
0
gcct_caseclassification
0
gcct_casedispositiontype
0
gcct_coachback
0
gcct_country
0
gcct_customersatisfactiontools
0
gcct_delegationofauthority
0
gcct_demandltrtpsmclaimsprocessing
0
gcct_doaprogramcode
0
gcct_documentcustomerrecontact
0
gcct_engine
0
gcct_executive
0
gcct_executiveliaison
0
gcct_fieldinvolvementassistancerequest
0
gcct_fmcccontract
0
gcct_fulfillmentvendor
0
gcct_genericinformation
0
gcct_genericinformationtopic
0
gcct_generictopic
0
gcct_goodfaithreview
0
gcct_knownpartsdelay
0
gcct_lemonlawcriteria
0
gcct_loanercost
0
gcct_loyaltyassistance
0
gcct_loyaltycostdetails
0
gcct_loyaltyprogramcode
0
gcct_mater

In [36]:
sqlCtx.table('account').select("message__id").show(10,False)


+---------------------------------+
|message__id                      |
+---------------------------------+
|08586581975786490962328736075CU45|
|08586582238534025880890828849CU10|
|08586581977153992263442686635CU00|
|08586581977157033421386414499CU44|
|08586581992744689562431102750CU03|
|08586582356616001493818426680CU47|
|08586581993807055188487338589CU43|
|08586581971075432766459714787CU06|
|08586582237778380601247371956CU06|
|08586582356613935885333232307CU03|
+---------------------------------+
only showing top 10 rows



In [65]:
sqlCtx.table('bad_record').filter(col("process__id")=="PN_9921757137954426").show(10,False)


+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [66]:
sqlCtx.table('bad_record').filter(col("process__id")=="PN_9921757137954426").where("entity_id like '%test%'").show(10,False)


AnalysisException: u"cannot resolve '`entity_id`' given input columns: [bad_record.datatype, bad_record.lastupdatedatetime, bad_record.reason, bad_record.data, bad_record.filename, bad_record.exception, bad_record.process__id, bad_record.lastupdtby, bad_record.message__id]; line 1 pos 0;\n'Filter 'entity_id LIKE %test%\n+- AnalysisBarrier\n      +- Filter (process__id#46821 = PN_9921757137954426)\n         +- SubqueryAlias bad_record\n            +- HiveTableRelation `dsc60230_gcct_tz_db`.`bad_record`, org.apache.hadoop.hive.ql.io.orc.OrcSerde, [data#46816, datatype#46817, filename#46818, reason#46819, exception#46820, process__id#46821, message__id#46822, lastupdtby#46823, lastupdatedatetime#46824]\n"

In [150]:
a.show(10,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [155]:
ff=[1,2]
gg=[1,"3",5]
ll=set(gg)


{2}

In [127]:
list(b.asDict().values()[0].encode('utf-8'))

['[',
 'e',
 'n',
 't',
 'i',
 't',
 'y',
 'l',
 'o',
 'g',
 'i',
 'c',
 'a',
 'l',
 'n',
 'a',
 'm',
 'e',
 ',',
 ' ',
 'e',
 'v',
 'e',
 'n',
 't',
 't',
 'y',
 'p',
 'e',
 ',',
 ' ',
 't',
 'i',
 'm',
 'e',
 'z',
 'o',
 'n',
 'e',
 'r',
 'u',
 'l',
 'e',
 'v',
 'e',
 'r',
 's',
 'i',
 'o',
 'n',
 'n',
 'u',
 'm',
 'b',
 'e',
 'r',
 ',',
 ' ',
 'e',
 'm',
 'a',
 'i',
 'l',
 '_',
 'i',
 'd',
 'e',
 'n',
 't',
 'i',
 't',
 'y',
 ',',
 ' ',
 'i',
 's',
 'w',
 'o',
 'r',
 'k',
 'f',
 'l',
 'o',
 'w',
 'c',
 'r',
 'e',
 'a',
 't',
 'e',
 'd',
 ',',
 ' ',
 's',
 'c',
 'h',
 'e',
 'd',
 'u',
 'l',
 'e',
 'd',
 's',
 't',
 'a',
 'r',
 't',
 ',',
 ' ',
 'i',
 's',
 'r',
 'e',
 'g',
 'u',
 'l',
 'a',
 'r',
 'a',
 'c',
 't',
 'i',
 'v',
 'i',
 't',
 'y',
 ',',
 ' ',
 'r',
 'e',
 'p',
 'l',
 'y',
 'c',
 'o',
 'u',
 'n',
 't',
 ',',
 ' ',
 'm',
 'o',
 'd',
 'i',
 'f',
 'i',
 'e',
 'd',
 'b',
 'y',
 ',',
 ' ',
 'm',
 'e',
 's',
 's',
 'a',
 'g',
 'e',
 'i',
 'd',
 ',',
 ' ',
 'a',
 'c',
 't',
 'u'

In [104]:
dp=[]
for i in a.collect():
    print(i.asDict().values()[0].encode('utf-8'))



[entitylogicalname, eventtype, timezoneruleversionnumber, email_identity, isworkflowcreated, scheduledstart, isregularactivity, replycount, modifiedby, messageid, actualend, ownerid, emailreminderexpirytime, slainvokedid_entitytype, conversationtrackingid, readreceiptrequested, traversedpath, emailsenderyominame, safedescription, createdonbehalfby, to, modifiedonbehalfby, utcconversiontimezonecode, createdon, attachmentcount, transactioncurrencyid_entitytype, onholdtime, sortdate, emailsendername, templateid, scheduleddurationminutes, parentactivityid_entitytype, messageiddupcheck, lastonholdtime, senton, sendersaccount_entitytype, owningbusinessunit, templateidname, serviceid_entitytype, serviceidname, owninguser, lastopenedtime, delayedemailsendtime, owningteam, activityid, deliveryprioritycode, owningteam_entitytype, transactioncurrencyidname, createdonbehalfbyyominame, emailsender_entitytype, description, category, versionnumber, sendersaccountyominame, owningbusinessunit_entitytyp

In [51]:
b=a.rdd.flatMap(lambda xs: [xs.split(",")])
b.collect()

Py4JJavaError: An error occurred while calling z:org.apache.spark.api.python.PythonRDD.collectAndServe.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 3 in stage 15.0 failed 4 times, most recent failure: Lost task 3.3 in stage 15.0 (TID 30, hpchdd2r01n14.hpc.ford.com, executor 12): org.apache.spark.api.python.PythonException: Traceback (most recent call last):
  File "/usr/hdp/current/spark2-client/python/pyspark/worker.py", line 229, in main
    process()
  File "/usr/hdp/current/spark2-client/python/pyspark/worker.py", line 224, in process
    serializer.dump_stream(func(split_index, iterator), outfile)
  File "/usr/hdp/current/spark2-client/python/pyspark/serializers.py", line 372, in dump_stream
    vs = list(itertools.islice(iterator, batch))
  File "<ipython-input-51-ae4c3d86d21a>", line 1, in <lambda>
  File "/usr/hdp/current/spark2-client/python/pyspark/sql/types.py", line 1561, in __getattr__
    raise AttributeError(item)
AttributeError: split

	at 

In [8]:
k='account'
v1=sqlCtx.table(k).select("entitystring")
df = v1.withColumn('New', udf1(v1.entitystring))
g1=df.agg({"New": "max"}).collect()[0].asDict()['max(New)']
g2=df.agg({"New": "min"}).collect()[0].asDict()['min(New)']
g3=len(sqlCtx.table(k).columns)
print("Column:"+str(k)+",Max:"+str(g1)+",Min:"+str(g2)+",Columns:"+str(g3))

Column:account,Max:282,Min:270,Columns:350


In [20]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:bad_record:[Row(count(1)=481)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=1)]
Table:email:[Row(count(1)=0)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=0)]
Table:systemuser:[Row(count(1)=0)]


In [27]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bkp%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('desc '+k).show(1000,False)
            print("Table:"+str(k))

+-----------------------------------------------------+--------------+-------+
|col_name                                             |data_type     |comment|
+-----------------------------------------------------+--------------+-------+
|account_identity                                     |int           |null   |
|account_rowversion                                   |string        |null   |
|id                                                   |string        |null   |
|sinkcreatedon                                        |timestamp     |null   |
|sinkmodifiedon                                       |timestamp     |null   |
|statecode                                            |int           |null   |
|statuscode                                           |int           |null   |
|customertypecode                                     |int           |null   |
|address1_freighttermscode                            |int           |null   |
|address1_addresstypecode                           

+---------------------------------------+--------------+-------+
|col_name                               |data_type     |comment|
+---------------------------------------+--------------+-------+
|appointment_identity                   |int           |null   |
|appointment_rowversion                 |string        |null   |
|id                                     |string        |null   |
|sinkcreatedon                          |timestamp     |null   |
|sinkmodifiedon                         |timestamp     |null   |
|statecode                              |int           |null   |
|statuscode                             |int           |null   |
|prioritycode                           |int           |null   |
|attachmenterrors                       |int           |null   |
|instancetypecode                       |int           |null   |
|isbilled                               |boolean       |null   |
|isregularactivity                      |boolean       |null   |
|gcct_dealerportal       

+----------------------------+---------+-------+
|col_name                    |data_type|comment|
+----------------------------+---------+-------+
|gcct_calendarrule_identity  |int      |null   |
|gcct_calendarrule_rowversion|string   |null   |
|id                          |string   |null   |
|calendarid                  |string   |null   |
|sinkcreatedon               |timestamp|null   |
|sinkmodifiedon              |timestamp|null   |
|createdby                   |string   |null   |
|createdby_entitytype        |string   |null   |
|modifiedby                  |string   |null   |
|modifiedby_entitytype       |string   |null   |
|createdon                   |timestamp|null   |
|description                 |string   |null   |
|duration                    |int      |null   |
|modifiedon                  |timestamp|null   |
|effectiveintervalend        |timestamp|null   |
|effectiveintervalstart      |timestamp|null   |
|endtime                     |timestamp|null   |
|effort             

+---------------------------------------+--------------+-------+
|col_name                               |data_type     |comment|
+---------------------------------------+--------------+-------+
|cxlvhlp_chatactivity_identity          |int           |null   |
|cxlvhlp_chatactivity_rowversion        |string        |null   |
|id                                     |string        |null   |
|sinkcreatedon                          |timestamp     |null   |
|sinkmodifiedon                         |timestamp     |null   |
|statecode                              |int           |null   |
|statuscode                             |int           |null   |
|community                              |int           |null   |
|instancetypecode                       |int           |null   |
|deliveryprioritycode                   |int           |null   |
|cxlvhlp_chatorigin                     |int           |null   |
|cxlvhlp_agentclienttype                |int           |null   |
|prioritycode            

+--------------------------------+--------------+-------+
|col_name                        |data_type     |comment|
+--------------------------------+--------------+-------+
|email_identity                  |int           |null   |
|email_rowversion                |string        |null   |
|id                              |string        |null   |
|sinkcreatedon                   |timestamp     |null   |
|sinkmodifiedon                  |timestamp     |null   |
|statecode                       |int           |null   |
|statuscode                      |int           |null   |
|notifications                   |int           |null   |
|emailreminderstatus             |int           |null   |
|emailremindertype               |int           |null   |
|deliveryprioritycode            |int           |null   |
|prioritycode                    |int           |null   |
|correlationmethod               |int           |null   |
|gcct_visibleoncustomerportal    |boolean       |null   |
|isworkflowcre

...

+-------------------------------------+--------------+-------+
|col_name                             |data_type     |comment|
+-------------------------------------+--------------+-------+
|id                                   |string        |null   |
|sinkcreatedon                        |timestamp     |null   |
|sinkmodifiedon                       |timestamp     |null   |
|statecode                            |int           |null   |
|statuscode                           |int           |null   |
|community                            |int           |null   |
|instancetypecode                     |int           |null   |
|msdyn_stage                          |int           |null   |
|deliveryprioritycode                 |int           |null   |
|prioritycode                         |int           |null   |
|msdyn_reminder                       |boolean       |null   |
|isworkflowcreated                    |boolean       |null   |
|isbilled                             |boolean       |n

+--------------------------------+--------------+-------+
|col_name                        |data_type     |comment|
+--------------------------------+--------------+-------+
|phonecall_identity              |int           |null   |
|phonecall_rowversion            |string        |null   |
|id                              |string        |null   |
|sinkcreatedon                   |timestamp     |null   |
|sinkmodifiedon                  |timestamp     |null   |
|statecode                       |int           |null   |
|statuscode                      |int           |null   |
|prioritycode                    |int           |null   |
|isbilled                        |boolean       |null   |
|isworkflowcreated               |boolean       |null   |
|gcct_visibleoncustomerportal    |boolean       |null   |
|gcct_visibleondealerportal      |boolean       |null   |
|directioncode                   |boolean       |null   |
|leftvoicemail                   |boolean       |null   |
|isregularacti

+--------------------------------+--------------+-------+
|col_name                        |data_type     |comment|
+--------------------------------+--------------+-------+
|slakpiinstance_identity         |int           |null   |
|slakpiinstance_rowversion       |string        |null   |
|id                              |string        |null   |
|sinkcreatedon                   |timestamp     |null   |
|sinkmodifiedon                  |timestamp     |null   |
|status                          |int           |null   |
|warningtimereached              |int           |null   |
|owninguser                      |string        |null   |
|owninguser_entitytype           |string        |null   |
|createdonbehalfby               |string        |null   |
|createdonbehalfby_entitytype    |string        |null   |
|transactioncurrencyid           |string        |null   |
|transactioncurrencyid_entitytype|string        |null   |
|regarding                       |string        |null   |
|regarding_ent

+-------------------------------------+--------------+-------+
|col_name                             |data_type     |comment|
+-------------------------------------+--------------+-------+
|systemuser_identity                  |int           |null   |
|systemuser_rowversion                |string        |null   |
|id                                   |string        |null   |
|sinkcreatedon                        |timestamp     |null   |
|sinkmodifiedon                       |timestamp     |null   |
|address1_addresstypecode             |int           |null   |
|address1_shippingmethodcode          |int           |null   |
|preferredemailcode                   |int           |null   |
|outgoingemaildeliverymethod          |int           |null   |
|preferredphonecode                   |int           |null   |
|emailrouteraccessapproval            |int           |null   |
|incomingemaildeliverymethod          |int           |null   |
|caltype                              |int           |n

+--------------------------------------------+--------------+-------+
|col_name                                    |data_type     |comment|
+--------------------------------------------+--------------+-------+
|team_identity                               |int           |null   |
|team_rowversion                             |string        |null   |
|id                                          |string        |null   |
|sinkcreatedon                               |timestamp     |null   |
|sinkmodifiedon                              |timestamp     |null   |
|gcct_businessteamtype                       |int           |null   |
|teamtype                                    |int           |null   |
|gcct_searchtabname                          |int           |null   |
|gcct_recordownershipbehavior                |int           |null   |
|gcct_defaultcontactaccountsetting           |string        |null   |
|systemmanaged                               |boolean       |null   |
|gcct_displaycaseond

In [3]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:account_bkp:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:annotation_bkp:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:calendar_bkp:[Row(count(1)=0)]
Table:contact:[Row(count(1)=0)]
Table:contact_bkp:[Row(count(1)=2)]
Table:email:[Row(count(1)=0)]
Table:email_bkp:[Row(count(1)=2)]
Table:fax:[Row(count(1)=0)]
Table:fax_bkp:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_caseassignment_bkp:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails_bkp:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_reactdata_bkp:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_recall_bkp:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:gcct_testdriverequest_bkp:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:incident_bkp:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=0)]
Table:phonecall_bkp:[Row(count(1)=0)]
Table:sy

In [7]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=1)]
Table:annotation:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=2)]
Table:email:[Row(count(1)=0)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=1)]
Table:systemuser:[Row(count(1)=4)]


In [26]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+":"+str(g1))

account:83483
annotation:4939
bad_record:200480
calendar:0
contact:3613
email:110
fax:92
gcct_caseassignment:0
gcct_loyaltycostdetails:0
gcct_reactdata:0
gcct_recall:0
gcct_testdriverequest:0
incident:2
msdyn_question:0
phonecall:57790
systemuser:86


In [32]:
print("data_captured_on,11/28/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,11/28/2018
Table,Data(rows)
account,16
annotation,18
appointment,5
bad_record,2365
calendar,0
calendarrule,0
contact,102
cxlvhlp_chatactivity,0
cxlvhlp_chatqueuestatistic,0
email,197
fax,0
gcct_caseassignment,0
gcct_documentcustomerrecontact,0
gcct_loyaltycostdetails,0
gcct_reactdata,0
gcct_recall,0
gcct_region,0
gcct_surveyconfiguration,0
gcct_testdriverequest,0
globaloptionsetmetadata,0
incident,0
letter,0
msdyn_answer,0
msdyn_question,0
msdyn_questionresponse,0
msdyn_survey,0
msdyn_surveyinvite,0
msdyn_surveyresponse,0
optionsetmetadata,0
phonecall,22
queueitem,96
slakpiinstance,2263
statemetadata,0
statusmetadata,0
systemuser,58
task,0
team,0
territory,0


In [16]:
sqlCtx.sql('desc formatted attributemetadata').show(1000,False)

+----------------------------+----------------------------------------------------------------------------------------------------+-------+
|col_name                    |data_type                                                                                           |comment|
+----------------------------+----------------------------------------------------------------------------------------------------+-------+
|id                          |bigint                                                                                              |null   |
|entityname                  |string                                                                                              |null   |
|attributename               |string                                                                                              |null   |
|attributetype               |string                                                                                              |null   |
|attributetypecode  

In [30]:
sqlCtx.sql('desc attributemetadata').show(1000,False)

AnalysisException: u"Table or view 'attributemetadata' not found in database 'dsc60230_gcct_tz_db';"

In [6]:
print("data_captured_on,11/20/2018")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,11/20/2018
Table,Data(rows)
account,83380
annotation,4870
bad_record,184463
calendar,0
contact,3558
email,5
fax,0
gcct_caseassignment,0
gcct_loyaltycostdetails,0
gcct_reactdata,0
gcct_recall,0
gcct_testdriverequest,0
incident,2
phonecall,57788
systemuser,73


In [5]:
print("data_captured_on,11/21/2018 2:22 PM")
print("Table,Data(rows)")
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k).select("count(1)").collect()[0].asDict().values()[0]
            print(str(k)+","+str(g1))

data_captured_on,11/21/2018 2:22 PM
Table,Data(rows)
account,0
activityparty,0
annotation,0
appointment,0
attributemetadata,0
bad_record,0
businessunit,0
contact,0


In [6]:
sqlContext.table("account").groupby("message__id").count().filter("count>1").show(100,False)


+-----------+-----+
|message__id|count|
+-----------+-----+
+-----------+-----+



In [14]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            v1=sqlCtx.table(k).select("entitystring")
            df = v1.withColumn('New', udf1(v1.entitystring))
            g1=df.agg({"New": "max"}).collect()[0].asDict()['max(New)']
            g2=df.agg({"New": "min"}).collect()[0].asDict()['min(New)']
            g3=len(sqlCtx.table(k).columns)
            print("table:"+str(k)+",Max_extractable_columns:"+str(g1)+",Min_extractable_columns:"+str(g2)+",Columns_in_table:"+str(g3))

table:account,Max_extractable_columns:351,Min_extractable_columns:271,Columns_in_table:351
table:account_bkp,Max_extractable_columns:282,Min_extractable_columns:270,Columns_in_table:350
table:annotation,Max_extractable_columns:61,Min_extractable_columns:60,Columns_in_table:58
table:annotation_bkp,Max_extractable_columns:60,Min_extractable_columns:59,Columns_in_table:57
table:calendar,Max_extractable_columns:None,Min_extractable_columns:None,Columns_in_table:26
table:calendar_bkp,Max_extractable_columns:27,Min_extractable_columns:27,Columns_in_table:25
table:contact,Max_extractable_columns:363,Min_extractable_columns:351,Columns_in_table:410
table:contact_bkp,Max_extractable_columns:417,Min_extractable_columns:361,Columns_in_table:409
table:email,Max_extractable_columns:155,Min_extractable_columns:155,Columns_in_table:152
table:email_bkp,Max_extractable_columns:154,Min_extractable_columns:153,Columns_in_table:151
table:fax,Max_extractable_columns:None,Min_extractable_columns:None,Column

In [7]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            sqlContext.table(k).groupby("message__id").count().filter("count>1").show(100,False)

data_captured_on,11/19/2018
Table,Data(rows)
+-----------+-----+
|message__id|count|
+-----------+-----+
+-----------+-----+

+-----------+-----+
|message__id|count|
+-----------+-----+
+-----------+-----+

+---------------------------------+-----+
|message__id                      |count|
+---------------------------------+-----+
|08586608192908332571165926039CU40|4    |
|08586608229187437786621989387CU45|4    |
|08586593491126130351598085664CU10|5    |
|08586608265389616802587728917CU09|4    |
|08586608192721786047773296826CU08|4    |
|08586608013581968366418539318CU33|4    |
|08586608083160984502596132261CU43|4    |
|08586608083882714524213732939CU32|4    |
|08586608049710054159145148839CU03|4    |
|08586608088505751856897313797CU33|4    |
|08586608086013740336709976651CU12|4    |
|08586608049741720535421592533CU12|4    |
|08586608122193352413427012154CU34|4    |
|08586608229182104652778554019CU45|4    |
|08586608158428505641220069716CU45|4    |
|08586608086017938392978409860CU46|4 

In [9]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%bkp%'").where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            sqlContext.table(k).groupby("shakey").count().filter("count>1").show(100,False)

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+

+------+-----+
|shakey|count|
+------+-----+
+------+-----+



In [15]:
a=sqlContext.table("bad_record")
a.groupby("reason").count().show(100,False)

+----------------------------------------------------------------+-----+
|reason                                                          |count|
+----------------------------------------------------------------+-----+
|Error Parsing gcct_socialmediaconversation                      |3    |
|Error Parsing systemuser                                        |1    |
|Error Parsing cxlvhlp_chatqueuestatistic                        |3    |
|Error Parsing slakpiinstance                                    |21   |
|Error Parsing gcct_goodfaithreview                              |4    |
|Error Parsing activityparty                                     |146  |
|Error Parsing gcct_vehicle                                      |6    |
|Duplicate record. Rejected by the process                       |7    |
|Error Parsing contact                                           |6    |
|Error Parsing task                                              |6    |
|Error Parsing gcct_warrantyloanerrequesthistory   

In [13]:
sqlContext.table("email_bkp").select("entitystring").show(2,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [40]:
sqlContext.sql("select fullname from contact_bkp ").show(10000,False)

+----------------------------------------------------------------------------------------+
|fullname                                                                                |
+----------------------------------------------------------------------------------------+
|RAMINDER B                                                                              |
|RAMINDER B                                                                              |
|LOUIS TAYLOR                                                                            |
|ELIZABETH DOMINGUEZ MURO                                                                |
|TERESA SMITH                                                                            |
|15557 LUNDY PKWY                                                                        |
|LOUIS TAYLOR                                                                            |
|RAMINDER B                                                                              |

In [27]:
sqlContext.sql("select count(*),datatype from bad_record group by datatype").show(10000,False)

+--------+---------------------------------+
|count(1)|datatype                         |
+--------+---------------------------------+
|10      |queueitem                        |
|6       |task                             |
|274     |gcct_knownpartsdelay             |
|4       |team                             |
|1       |contact                          |
|75      |activityparty                    |
|73      |Entity                           |
|6       |gcct_vehicle                     |
|2       |gcct_socialmediaconversation     |
|1       |gcct_warrantyloanerrequesthistory|
|2       |gcct_socialmediamessage          |
|3       |cxlvhlp_chatqueuestatistic       |
|3       |cxlvhlp_chatactivity             |
|14      |gcct_warrantyloanerrequest       |
|4       |gcct_onlinegaragevehicles        |
|1       |gcct_loyaltyassistance           |
|1       |gcct_queuepriority               |
|1       |gcct_warrantyloanerpartsdelay    |
+--------+---------------------------------+



In [29]:
sqlContext.sql("select datatype from bad_record where datatype ='entity' ").show(10000,False)

+--------+
|datatype|
+--------+
+--------+



In [6]:
sqlContext.sql("select * from contact where hex(entitystring) like '%0A%' ").show(2,False)

+----------------+------------------+------------------------------------+-------------------+-------------------+---------+----------+-----------------------+---------------+----------------+-------------------------+----------+------------------------+------------------+-------------------------+----------------------------+---------------+-------------------+-------------------------+----------------+---------------+-------------------------+---------------------------+----------------+-----------------------+--------------------------+--------------+---------------------------+---------------------------+----------------+------------------------+---------------------------+-------------+------------------------+----------------+-------------+---------------------------+--------------------+----------------------+-------------------+---------------+-------------------+---------------------------------+-------------+------------+----------------+------------------------+-------------

In [7]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k+' where hex(entitystring) like "%0D%"').collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=0)]
Table:email:[Row(count(1)=0)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=0)]
Table:systemuser:[Row(count(1)=0)]


In [8]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k+' where hex(entitystring) like "%C2A0%"').collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=2)]
Table:email:[Row(count(1)=1124)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=36)]
Table:systemuser:[Row(count(1)=0)]


In [12]:
sqlContext.sql("select entitystring from contact where hex(entitystring) like '%C2A0%' ").show(2,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [10]:
sqlContext.sql("select hex(address1_line1) from contact where hex(entitystring) like '%C2A0%' ").show(2,False)

+--------------------------------------------------+
|hex(address1_line1)                               |
+--------------------------------------------------+
|4341525245542E204D4F434849532041484F4D45C2A0532D4E|
|4341525245542E204D4F434849532041484F4D45C2A0532D4E|
+--------------------------------------------------+



In [63]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            print('####')
            print(k)
            sqlCtx.sql('desc '+k).show(1000,False)

####
account
+-----------------------------------------------------+--------------+-------+
|col_name                                             |data_type     |comment|
+-----------------------------------------------------+--------------+-------+
|account_identity                                     |int           |null   |
|account_rowversion                                   |string        |null   |
|id                                                   |string        |null   |
|sinkcreatedon                                        |timestamp     |null   |
|sinkmodifiedon                                       |timestamp     |null   |
|statecode                                            |int           |null   |
|statuscode                                           |int           |null   |
|address1_addresstypecode                             |int           |null   |
|address1_shippingmethodcode                          |int           |null   |
|gcct_accountstatus                    

+------------------------------------+---------+-------+
|col_name                            |data_type|comment|
+------------------------------------+---------+-------+
|gcct_calendar_identity              |int      |null   |
|gcct_calendar_rowversion            |string   |null   |
|id                                  |string   |null   |
|sinkcreatedon                       |timestamp|null   |
|sinkmodifiedon                      |timestamp|null   |
|createdby                           |string   |null   |
|createdby_entitytype                |string   |null   |
|modifiedby                          |string   |null   |
|modifiedby_entitytype               |string   |null   |
|createdon                           |timestamp|null   |
|description                         |string   |null   |
|modifiedon                          |timestamp|null   |
|name                                |string   |null   |
|businessunitid                      |string   |null   |
|businessunitid_entitytype     

+--------------------------------+--------------+-------+
|col_name                        |data_type     |comment|
+--------------------------------+--------------+-------+
|email_identity                  |int           |null   |
|email_rowversion                |string        |null   |
|id                              |string        |null   |
|sinkcreatedon                   |timestamp     |null   |
|sinkmodifiedon                  |timestamp     |null   |
|statecode                       |int           |null   |
|statuscode                      |int           |null   |
|notifications                   |int           |null   |
|emailreminderstatus             |int           |null   |
|emailremindertype               |int           |null   |
|deliveryprioritycode            |int           |null   |
|prioritycode                    |int           |null   |
|correlationmethod               |int           |null   |
|gcct_visibleoncustomerportal    |boolean       |null   |
|isworkflowcre

+---------------------------------+---------+-------+
|col_name                         |data_type|comment|
+---------------------------------+---------+-------+
|gcct_reactdata_identity          |int      |null   |
|gcct_reactdata_rowversion        |string   |null   |
|id                               |string   |null   |
|sinkcreatedon                    |timestamp|null   |
|sinkmodifiedon                   |timestamp|null   |
|statecode                        |int      |null   |
|statuscode                       |int      |null   |
|gcct_ereactstatusdescription     |int      |null   |
|gcct_usedvehpermanentlydisabled  |boolean  |null   |
|gcct_rotemporarilydisable        |boolean  |null   |
|gcct_transmitsusedvehunderpa     |boolean  |null   |
|gcct_inventorypermanentlydisabled|boolean  |null   |
|gcct_padoesnotsendinvoices       |boolean  |null   |
|gcct_transmitsinvoicesunderpa    |boolean  |null   |
|gcct_padoesnotsendinventory      |boolean  |null   |
|gcct_inventorytemporarilydi

+-------------------------------------------------+--------------+-------+
|col_name                                         |data_type     |comment|
+-------------------------------------------------+--------------+-------+
|incident_identity                                |int           |null   |
|incident_rowversion                              |string        |null   |
|id                                               |string        |null   |
|sinkcreatedon                                    |timestamp     |null   |
|sinkmodifiedon                                   |timestamp     |null   |
|statecode                                        |int           |null   |
|statuscode                                       |int           |null   |
|caseorigincode                                   |int           |null   |
|customersatisfactioncode                         |int           |null   |
|gcct_cancellationtype                            |int           |null   |
|messagetypecode         

In [37]:
sqlCtx.sql('select fullname,id,lastupdatedatetime,oozieid,count(*) from contact group by fullname,id,lastupdatedatetime,oozieid having count(*)==11 ').show(1000,False)

+--------------+------------------------------------+-------------------+------------------------------------+--------+
|fullname      |id                                  |lastupdatedatetime |oozieid                             |count(1)|
+--------------+------------------------------------+-------------------+------------------------------------+--------+
|LOUIS TAYLOR  |27C7D66F-BF86-E811-A83F-000D3A37C8E1|2018-09-07 10:57:36|0065220-180727235812092-oozie-oozi-W|11      |
|HARDEEPAK SHAH|06D5FEFE-D7B1-E811-A83F-000D3A37CC26|2018-09-24 14:01:43|0023320-180910131225633-oozie-oozi-W|11      |
+--------------+------------------------------------+-------------------+------------------------------------+--------+



In [9]:
sqlCtx.sql('select id,shakey,lastupdatedatetime,oozieid,count(*) from account group by id,shakey,lastupdatedatetime,oozieid having count(*) >1 ').show(100,False)

+------------------------------------+----------------------------------------------------------------+-------------------+------------------------------------+--------+
|id                                  |shakey                                                          |lastupdatedatetime |oozieid                             |count(1)|
+------------------------------------+----------------------------------------------------------------+-------------------+------------------------------------+--------+
|CF0CDAC7-90B5-E811-A83F-000D3A37CC26|99dbe261481f4140d28d622c84a639fd40d812e613fd772a892c35b1467b2032|2018-09-11 06:06:11|0001244-180910131225633-oozie-oozi-W|2       |
|272F2475-99BA-E811-A842-000D3A37C740|50474bf707e25858038098b99dbcde7e67753509c05de33e06085d96432c557a|2018-09-19 06:01:27|0013067-180910131225633-oozie-oozi-W|2       |
+------------------------------------+----------------------------------------------------------------+-------------------+---------------------------

In [10]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            stmnt='select id,shakey,lastupdatedatetime,oozieid,count(*) from '+k+' group by id,shakey,lastupdatedatetime,oozieid having count(*) >1 '
            a=sqlCtx.sql(stmnt).count()
            print("Table: "+str(k)+" has "+str(a)+" duplicates")

Table: account has 2 duplicates
Table: annotation has 212 duplicates
Table: calendar has 1 duplicates
Table: contact has 134 duplicates
Table: email has 1 duplicates
Table: fax has 0 duplicates
Table: gcct_caseassignment has 18 duplicates
Table: gcct_loyaltycostdetails has 4 duplicates
Table: gcct_reactdata has 0 duplicates
Table: gcct_recall has 1 duplicates
Table: gcct_testdriverequest has 0 duplicates
Table: incident has 101 duplicates
Table: phonecall has 3 duplicates
Table: systemuser has 1 duplicates


In [52]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            a=sqlContext.table(k).where(col("lastupdatedatetime").like("%2018-09-24%")).groupby("id","shakey").count().filter(col('count')>1).count()
            print("Table: "+str(k)+" has "+str(a)+" duplicates")

Table: account has 1 duplicates
Table: annotation has 0 duplicates
Table: calendar has 0 duplicates
Table: contact has 0 duplicates
Table: email has 0 duplicates
Table: fax has 0 duplicates
Table: gcct_caseassignment has 0 duplicates
Table: gcct_loyaltycostdetails has 0 duplicates
Table: gcct_reactdata has 0 duplicates
Table: gcct_recall has 0 duplicates
Table: gcct_testdriverequest has 0 duplicates
Table: incident has 0 duplicates
Table: phonecall has 0 duplicates
Table: systemuser has 0 duplicates


In [51]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            a=sqlContext.table(k).where(col("lastupdatedatetime").like("%2018-09-26%")).groupby("id","shakey").count().filter(col('count')>1).count()
            print("Table: "+str(k)+" has "+str(a)+" duplicates")

Table: account has 1 duplicates
Table: annotation has 0 duplicates
Table: calendar has 0 duplicates
Table: contact has 0 duplicates
Table: email has 0 duplicates
Table: fax has 0 duplicates
Table: gcct_caseassignment has 0 duplicates
Table: gcct_loyaltycostdetails has 0 duplicates
Table: gcct_reactdata has 0 duplicates
Table: gcct_recall has 0 duplicates
Table: gcct_testdriverequest has 0 duplicates
Table: incident has 0 duplicates
Table: phonecall has 0 duplicates
Table: systemuser has 1 duplicates


In [10]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            a=sqlContext.table(k).where(col("lastupdatedatetime").like("%2018-09-25%")).groupby("id","shakey").count().filter(col('count')>1).count()
            print("Table: "+str(k)+" has "+str(a)+" duplicates")

Table: account has 0 duplicates
Table: annotation has 0 duplicates
Table: calendar has 0 duplicates
Table: contact has 0 duplicates
Table: email has 0 duplicates
Table: fax has 0 duplicates
Table: gcct_caseassignment has 0 duplicates
Table: gcct_loyaltycostdetails has 0 duplicates
Table: gcct_reactdata has 0 duplicates
Table: gcct_recall has 0 duplicates
Table: gcct_testdriverequest has 0 duplicates
Table: incident has 1 duplicates
Table: phonecall has 0 duplicates
Table: systemuser has 0 duplicates


In [59]:
sqlContext.sql("desc incident").select('col_name').where("col_name like '%priority%'").show(100,False)

+------------+
|col_name    |
+------------+
|prioritycode|
+------------+



In [57]:
sqlContext.table('account').where(col("lastupdatedatetime").like("%2018-09-26%")).groupby("id","shakey").count().filter(col('count')>1).show(10,False)

+------------------------------------+----------------------------------------------------------------+-----+
|id                                  |shakey                                                          |count|
+------------------------------------+----------------------------------------------------------------+-----+
|8190E634-4284-E811-A83D-000D3A37C740|a240c5e3d8a0ae3f7d0e4d31852d5a757b65cfc676d542ec13686a92e007bbf0|2    |
+------------------------------------+----------------------------------------------------------------+-----+



In [58]:
sqlContext.table('account').where(col("lastupdatedatetime").like("%2018-09-26%")).filter(col('shakey')=='a240c5e3d8a0ae3f7d0e4d31852d5a757b65cfc676d542ec13686a92e007bbf0').show(10,False)

+----------------+------------------+------------------------------------+-------------------+-------------------+---------+----------+------------------------+---------------------------+------------------+---------------+-------------------------+-----------------+----------------------------+-------------------------+----------------+--------------------------+-------------+------------------------+----------------+------------------+----------------+---------------+----------------+-------------------+------------+---------------------------+---------------------------+-------------------------+-------------+---------------+------------+-------------------+------------------------------+------------------------+--------------+--------+----------+-------------------+-------------+-----------+------+----------+-----------+----------------------+---------+---------------------+--------------------------------+---------------------------+--------------------------------------+---------

In [96]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k+' where hex(entitystring) like "%0D%"').collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=0)]
Table:email:[Row(count(1)=0)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=0)]
Table:systemuser:[Row(count(1)=0)]


In [97]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").collect():
            k=m.asDict().values()[0].encode('utf-8')
            g1=sqlCtx.sql('select count(*) from '+k+' where hex(entitystring) like "%C2A0%"').collect()
            print("Table:"+str(k)+":"+str(g1))

Table:account:[Row(count(1)=0)]
Table:annotation:[Row(count(1)=0)]
Table:calendar:[Row(count(1)=0)]
Table:contact:[Row(count(1)=2)]
Table:email:[Row(count(1)=400)]
Table:fax:[Row(count(1)=0)]
Table:gcct_caseassignment:[Row(count(1)=0)]
Table:gcct_loyaltycostdetails:[Row(count(1)=0)]
Table:gcct_reactdata:[Row(count(1)=0)]
Table:gcct_recall:[Row(count(1)=0)]
Table:gcct_testdriverequest:[Row(count(1)=0)]
Table:incident:[Row(count(1)=0)]
Table:phonecall:[Row(count(1)=9)]
Table:systemuser:[Row(count(1)=0)]


In [3]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").where("tableName like '%bkp%'").collect():
        k=m.asDict().values()[0].encode('utf-8')
        for b in sqlCtx.sql('desc '+k).filter(col("data_type") == "string").filter(col("col_name") != "entitystring").select("col_name").collect():
                c=b.asDict().values()[0].encode('utf-8')
                s=sqlContext.sql('select max(length('+c+')),min(length('+c+')) from dsc60230_gcct_tz_db.'+k).collect()
                if str(s[0].asDict().values()[1]) != "None":
                    print(k+','+c+','+str(s[0].asDict().values()))

account_bkp,account_rowversion,[12, 12]
account_bkp,id,[36, 36]
account_bkp,gcct_dealerservicemanagerid,[36, 36]
account_bkp,gcct_dealerservicemanagerid_entitytype,[7, 7]
account_bkp,owningbusinessunit,[36, 36]
account_bkp,owningbusinessunit_entitytype,[12, 12]
account_bkp,territoryid,[36, 36]
account_bkp,territoryid_entitytype,[9, 9]
account_bkp,primarycontactid,[36, 36]
account_bkp,primarycontactid_entitytype,[7, 7]
account_bkp,gcct_dealercontact,[36, 36]
account_bkp,gcct_dealercontact_entitytype,[7, 7]
account_bkp,modifiedby,[36, 36]
account_bkp,modifiedby_entitytype,[10, 10]
account_bkp,modifiedonbehalfby,[36, 36]
account_bkp,modifiedonbehalfby_entitytype,[10, 10]
account_bkp,gcct_region,[36, 36]
account_bkp,gcct_region_entitytype,[11, 11]
account_bkp,owninguser,[36, 36]
account_bkp,owninguser_entitytype,[10, 10]
account_bkp,owningteam,[36, 36]
account_bkp,owningteam_entitytype,[4, 4]
account_bkp,transactioncurrencyid,[36, 36]
account_bkp,transactioncurrencyid_entitytype,[19, 19]
a

contact_bkp,gcct_stag2,[7, 7]
contact_bkp,gcct_ltag1,[7, 7]
contact_bkp,emailaddress3,[38, 7]
contact_bkp,emailaddress2,[39, 7]
contact_bkp,emailaddress1,[2, 76]
contact_bkp,nickname,[7, 3]
contact_bkp,lastname,[50, 1]
contact_bkp,telephone1,[0, 14]
contact_bkp,adx_identity_passwordhash,[68, 68]
contact_bkp,gcct_stag1,[7, 7]
contact_bkp,address2_addressid,[36, 36]
contact_bkp,address1_composite,[1, 149]
contact_bkp,msdyusd_currentprofile,[4, 4]
contact_bkp,owneridyominame,[25, 8]
contact_bkp,address1_line1,[100, 1]
contact_bkp,mastercontactidyominame,[9, 14]
contact_bkp,address1_country,[2, 32]
contact_bkp,firstname,[47, 1]
contact_bkp,suffix,[10, 2]
contact_bkp,gcct_contactpreferenceupdatebyuseridyominame,[25, 9]
contact_bkp,parentcustomeridyominame,[16, 7]
contact_bkp,msdyusd_facebook,[8, 8]
contact_bkp,contactid,[36, 36]
contact_bkp,address1_line2,[1, 39]
contact_bkp,gcct_surveysuppressionsetbyuseridyominame,[9, 25]
contact_bkp,modifiedbyyominame,[25, 9]
contact_bkp,gcct_datasources

gcct_loyaltycostdetails_bkp,modifiedby_entitytype,[10, 10]
gcct_loyaltycostdetails_bkp,owninguser,[36, 36]
gcct_loyaltycostdetails_bkp,owninguser_entitytype,[10, 10]
gcct_loyaltycostdetails_bkp,owningbusinessunit,[36, 36]
gcct_loyaltycostdetails_bkp,owningbusinessunit_entitytype,[12, 12]
gcct_loyaltycostdetails_bkp,ownerid,[36, 36]
gcct_loyaltycostdetails_bkp,ownerid_entitytype,[4, 10]
gcct_loyaltycostdetails_bkp,gcct_name,[41, 77]
gcct_loyaltycostdetails_bkp,modifiedbyyominame,[20, 9]
gcct_loyaltycostdetails_bkp,gcct_agentnameidyominame,[9, 9]
gcct_loyaltycostdetails_bkp,gcct_rolinenumber,[6, 1]
gcct_loyaltycostdetails_bkp,gcct_rejectiondetails,[20, 20]
gcct_loyaltycostdetails_bkp,gcct_approvalrejectioncode,[4, 4]
gcct_loyaltycostdetails_bkp,owneridyominame,[12, 9]
gcct_loyaltycostdetails_bkp,gcct_loyaltycostdetailsid,[36, 36]
gcct_loyaltycostdetails_bkp,createdbyyominame,[9, 12]
gcct_loyaltycostdetails_bkp,modifiedonbehalfbyyominame,[12, 9]
gcct_loyaltycostdetails_bkp,lastupdtby,[8, 

incident_bkp,owninguser,[36, 36]
incident_bkp,owninguser_entitytype,[10, 10]
incident_bkp,slainvokedid,[36, 36]
incident_bkp,msa_partnercontactid,[36, 36]
incident_bkp,msa_partnercontactid_entitytype,[7, 7]
incident_bkp,gcct_customercountryid,[36, 36]
incident_bkp,gcct_customercountryid_entitytype,[12, 12]
incident_bkp,gcct_surveysenttocontact,[36, 36]
incident_bkp,gcct_surveysenttocontact_entitytype,[7, 7]
incident_bkp,gcct_lincolncsm,[36, 36]
incident_bkp,gcct_lincolncsm_entitytype,[10, 10]
incident_bkp,gcct_closedby,[36, 36]
incident_bkp,gcct_closedby_entitytype,[10, 10]
incident_bkp,modifiedonbehalfby,[36, 36]
incident_bkp,modifiedonbehalfby_entitytype,[10, 10]
incident_bkp,primarycontactid,[36, 36]
incident_bkp,primarycontactid_entitytype,[7, 7]
incident_bkp,gcct_reopenedby,[36, 36]
incident_bkp,gcct_reopenedby_entitytype,[10, 10]
incident_bkp,gcct_fmcccontract,[36, 36]
incident_bkp,gcct_fmcccontract_entitytype,[17, 17]
incident_bkp,parentcaseid,[36, 36]
incident_bkp,parentcaseid_

systemuser_bkp,windowsliveid,[37, 12]
systemuser_bkp,address1_postalcode,[5, 10]
systemuser_bkp,address1_composite,[33, 81]
systemuser_bkp,address2_addressid,[36, 36]
systemuser_bkp,address1_fax,[13, 13]
systemuser_bkp,createdbyyominame,[15, 15]
systemuser_bkp,fullname,[6, 45]
systemuser_bkp,modifiedonbehalfbyyominame,[25, 8]
systemuser_bkp,defaultodbfoldername,[11, 3]
systemuser_bkp,lastupdtby,[8, 8]
systemuser_bkp,shakey,[64, 64]
systemuser_bkp,oozieid,[36, 36]


In [89]:
for m in sqlContext.tables("dsc60230_gcct_tz_db").select('tableName').where("tableName not like '%temptz%'").where("tableName not like '%bad%'").where("tableName not like '%bkp%'").collect():
        k=m.asDict().values()[0].encode('utf-8')
        print(k)

account
annotation
calendar
contact
email
fax
gcct_caseassignment
gcct_loyaltycostdetails
gcct_reactdata
gcct_recall
gcct_testdriverequest
incident
phonecall
systemuser


In [11]:
sqlContext.table('account').where("process__id = 'PN_8131633011058713'").where("message__id like '%est%'").select("message__id","entitystring").show(1000,False)

+-----------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [15]:
sqlContext.table('incident').where("process__id = 'PN_8131633011058713'").where("message__id like '%est%'").select("message__id","entitystring").show(1000,False)

+-----------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [10]:
sqlContext.table('annotation').where("process__id = 'PN_8131633011058713'").select("message__id","entitystring").show(1000,False)

+-----------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [14]:
sqlContext.table('bad_record').where("process__id ='PN_8131633011058713'").show(1000,False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------